In [1]:
#Importing libraries
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
# Input data files are available in the "../input/" directory.
import os
import matplotlib.pyplot as plt#visualization
from PIL import  Image
%matplotlib inline
import pandas as pd
import seaborn as sns#visualization
import itertools
import warnings
warnings.filterwarnings("ignore")
import io
import plotly.offline as py#visualization
py.init_notebook_mode(connected=True)#visualization
import plotly.graph_objs as go#visualization
import plotly.tools as tls#visualization
import plotly.figure_factory as ff#visualization

# 1.Data

In [2]:
coupon=pd.read_csv('L2_Week3.csv')
coupon.head()

ID  age         job   marital default returned loan  \
0   1   43  management   married      no      yes   no   
1   2   42  technician  divorced      no      yes   no   
2   3   47      admin.   married      no      yes  yes   
3   4   28  management    single      no      yes  yes   
4   5   42  technician  divorced      no      yes   no   

   coupon_used_in_last6_month  coupon_used_in_last_month  coupon_ind  
0                           2                          0           0  
1                           1                          1           0  
2                           2                          0           0  
3                           2                          0           0  
4                           5                          0           0

1.1 Data overview

In [3]:
print ("Rows     : " ,coupon.shape[0])
print ("Columns  : " ,coupon.shape[1])
print ("\nFeatures : \n" ,coupon.columns.tolist())
print ("\nMissing values :  ", coupon.isnull().sum().values.sum())
print ("\nUnique values :  \n",coupon.nunique())

('Rows     : ', 25317)
('Columns  : ', 10)
('\nFeatures : \n', ['ID', 'age', 'job', 'marital', 'default', 'returned', 'loan', 'coupon_used_in_last6_month', 'coupon_used_in_last_month', 'coupon_ind'])
('\nMissing values :  ', 0)
('\nUnique values :  \n', ID                            25317
age                              75
job                              12
marital                           3
default                           2
returned                          2
loan                              2
coupon_used_in_last6_month       43
coupon_used_in_last_month        13
coupon_ind                        2
dtype: int64)


# 2. Data Manipulation

In [4]:
coupon=coupon.rename(columns={'coupon_ind':'coupon_use'})
# Age to categorical column
def age_lab(coupon) :
    
    if coupon["age"] <= 12 :
        return "Age_0-18"
    elif (coupon["age"] > 12) & (coupon["age"] <= 24 ):
        return "Age_18-24"
    elif (coupon["age"] > 24) & (coupon["age"] <= 38) :
        return "Age_24-38"
    elif (coupon["age"] > 48) & (coupon["age"] <= 50) :
        return "Age_38-50"
    elif coupon["age"] > 50 :
        return "Age_gt_50"
coupon["age_group"] = coupon.apply(lambda coupon:age_lab(coupon),
                                      axis = 1)
#Seperate use and non use customers
use= coupon[coupon["coupon_use"] == 1]
not_use= coupon[coupon["coupon_use"] == 0]

#Separating catagorical and numerical columns 
Id_col = ['ID']
target_col = ['coupon_use']
cat_cols = coupon.nunique()[coupon.nunique()<13].keys().tolist()
cat_cols = [x for x in cat_cols if x not in target_col]
num_cols = [x for x in coupon.columns if x not in cat_cols + target_col + Id_col]

# 3. Exploratory Data Analysis

3.1 Customer coupon use in data

In [5]:
import os

if not os.path.exists("images"):
    os.mkdir("images")
#labels
lab = coupon['coupon_use'].value_counts().keys().tolist()
#values
val = coupon['coupon_use'].value_counts().values.tolist()

trace = go.Pie(labels = lab ,
               values = val ,
               marker = dict(colors =  [ 'royalblue' ,'lime'],
                             line = dict(color = "white",
                                         width =  1.3)
                            ),
               rotation = 90,
               hoverinfo = "label+value+text",
               hole = .5
              )
layout = go.Layout(dict(title = "Customer coupon use in data",
                        plot_bgcolor  = "rgb(243,243,243)",
                        paper_bgcolor = "rgb(243,243,243)",
                       )
                  )

data = [trace]
fig = go.Figure(data = data,layout = layout)
py.iplot(fig)

3.2 Variables distribution in customer coupon use

In [6]:
#pie plot for customer type
def plot_pie(column) :
    
    trace1 = go.Pie(values  = use[column].value_counts().values.tolist(),
                    labels  = use[column].value_counts().keys().tolist(),
                    hoverinfo = "label+percent+name",
                    domain  = dict(x = [0,.48]),
                    name    = "Used Customers",
                    marker  = dict(line = dict(width = 2,
                                               color = "rgb(243,243,243)")
                                  ),
                    hole    = .6
                   )
    trace2 = go.Pie(values  = not_use[column].value_counts().values.tolist(),
                    labels  = not_use[column].value_counts().keys().tolist(),
                    hoverinfo = "label+percent+name",
                    marker  = dict(line = dict(width = 2,
                                               color = "rgb(243,243,243)")
                                  ),
                    domain  = dict(x = [.52,1]),
                    hole    = .6,
                    name    = "Non use customers" 
                   )


    layout = go.Layout(dict(title = column + " distribution in customer attrition ",
                            plot_bgcolor  = "rgb(243,243,243)",
                            paper_bgcolor = "rgb(243,243,243)",
                            annotations = [dict(text = "Used Customers",
                                                font = dict(size = 13),
                                                showarrow = False,
                                                x = .15, y = .5),
                                           dict(text = "Non use customers",
                                                font = dict(size = 13),
                                                showarrow = False,
                                                x = .88,y = .5
                                               )
                                          ]
                           )
                      )
    data = [trace1,trace2]
    fig  = go.Figure(data = data,layout = layout)
    py.iplot(fig)
for i in cat_cols :
    plot_pie(i)

# histogram for customer type
def histogram(column) :
    trace1 = go.Histogram(x  = use[column],
                          histnorm= "percent",
                          name = "Used Customers",
                          marker = dict(line = dict(width = .5,
                                                    color = "black"
                                                    )
                                        ),
                         opacity = .9 
                         ) 
    
    trace2 = go.Histogram(x  = not_use[column],
                          histnorm = "percent",
                          name = "Non use customers",
                          marker = dict(line = dict(width = .5,
                                              color = "black"
                                             )
                                 ),
                          opacity = .9
                         )
    
    data = [trace1,trace2]
    layout = go.Layout(dict(title =column + " distribution in customer attrition ",
                            plot_bgcolor  = "rgb(243,243,243)",
                            paper_bgcolor = "rgb(243,243,243)",
                            xaxis = dict(gridcolor = 'rgb(255, 255, 255)',
                                             title = column,
                                             zerolinewidth=1,
                                             ticklen=5,
                                             gridwidth=2
                                            ),
                            yaxis = dict(gridcolor = 'rgb(255, 255, 255)',
                                             title = "percent",
                                             zerolinewidth=1,
                                             ticklen=5,
                                             gridwidth=2
                                            ),
                           )
                      )
    fig  = go.Figure(data=data,layout=layout)
    
    pie = py.iplot(fig)
for i in num_cols :
    histogram(i)
    his = histogram(i)

# Scatter plot matrix for numerical columns in data
def scatter_matrix(df)  :
    
    df  = df.sort_values(by = "coupon_use" ,ascending = True)
    classes = df["coupon_use"].unique().tolist()
    classes
    
    class_code  = {classes[k] : k for k in range(2)}
    class_code

    color_vals = [class_code[cl] for cl in df["coupon_use"]]
    color_vals

    pl_colorscale = "Portland"

    pl_colorscale

    text = [df.loc[k,"coupon_use"] for k in range(len(df))]
    text

    trace = go.Splom(dimensions = [dict(label  = "age",
                                       values = df["age"]),
                                  dict(label  = 'Coupon used in last 6 month',
                                       values = df['coupon_used_in_last6_month']),
                                  dict(label  = 'Coupon used in last month',
                                       values = df['coupon_used_in_last_month'])],
                     text = text,
                     marker = dict(color = color_vals,
                                   colorscale = pl_colorscale,
                                   size = 3,
                                   showscale = False,
                                   line = dict(width = .1,
                                               color='rgb(230,230,230)'
                                              )
                                  )
                    )
    axis = dict(showline  = True,
                zeroline  = False,
                gridcolor = "#fff",
                ticklen   = 4
               )
    
    layout = go.Layout(dict(title  = 
                            "Scatter plot matrix for Numerical columns for customer type",
                            autosize = False,
                            height = 800,
                            width  = 800,
                            dragmode = "select",
                            hovermode = "closest",
                            plot_bgcolor  = 'rgba(240,240,240, 0.95)',
                            xaxis1 = dict(axis),
                            yaxis1 = dict(axis),
                            xaxis2 = dict(axis),
                            yaxis2 = dict(axis),
                            xaxis3 = dict(axis),
                            yaxis3 = dict(axis),
                           )
                      )
    data   = [trace]
    fig = go.Figure(data = data,layout = layout )
    py.iplot(fig)
scatter_matrix(coupon)

In [7]:
#Data Preprocessing
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import StandardScaler
#Copy data
df_coupon = coupon.copy()
coupon = coupon.drop(columns = "age_group")
#customer id col
Id_col     = ['ID']
#Target columns
target_col = ["coupon_use"]
#categorical columns
cat_cols   = coupon.nunique()[coupon.nunique() < 13].keys().tolist()
cat_cols   = [x for x in cat_cols if x not in target_col]
#numerical columns
num_cols   = [x for x in coupon.columns if x not in cat_cols + target_col + Id_col]
#Binary columns with 2 values
bin_cols   = coupon.nunique()[coupon.nunique() == 2].keys().tolist()
#Columns more than 2 values
multi_cols = [i for i in cat_cols if i not in bin_cols]

#Label encoding Binary columns
le = LabelEncoder()
for i in bin_cols :
    coupon[i] = le.fit_transform(coupon[i])
    
#Duplicating columns for multi value columns
coupon = pd.get_dummies(data = coupon,columns = multi_cols )
coupon.drop(['job_unknown'],axis=1,inplace=True) 
#Scaling Numerical columns
std = StandardScaler()
scaled = std.fit_transform(coupon[num_cols])
scaled = pd.DataFrame(scaled,columns=num_cols)

#dropping original values merging scaled values for numerical columns
df_coupon_og = coupon.copy()
coupon = coupon.drop(columns = num_cols,axis = 1)
coupon = coupon.drop(columns = 'ID',axis = 1)
coupon = coupon.merge(scaled,left_index=True,right_index=True,how = "left")

3.4 Correlation Matrix

In [8]:
#correlation
correlation = coupon.corr()
#tick labels
matrix_cols = correlation.columns.tolist()
#convert to array
corr_array  = np.array(correlation)

#Plotting
trace = go.Heatmap(z = corr_array,
                   x = matrix_cols,
                   y = matrix_cols,
                   colorscale = "Viridis",
                   colorbar   = dict(title = "Pearson Correlation coefficient",
                                     titleside = "right"
                                    ) ,
                  )

layout = go.Layout(dict(title = "Correlation Matrix for variables",
                        autosize = False,
                        height  = 720,
                        width   = 800,
                        margin  = dict(r = 0 ,l = 210,
                                       t = 25,b = 210,
                                      ),
                        yaxis   = dict(tickfont = dict(size = 9)),
                        xaxis   = dict(tickfont = dict(size = 9))
                       )
                  )

data = [trace]
fig = go.Figure(data=data,layout=layout)
py.iplot(fig)

3.5 Binary variables distribution in customer coupon use(Radar Chart)

In [9]:
#separating binary columns
bi_cs = coupon.nunique()[coupon.nunique() == 2].keys()
dat_rad = coupon[bi_cs]

#plotting radar chart for used and non use customers(binary variables)
def plot_radar(df,aggregate,title) :
    data_frame = df[df["coupon_use"] == aggregate] 
    data_frame_x = data_frame[bi_cs].sum().reset_index()
    data_frame_x.columns  = ["feature","1"]
    data_frame_x["0"]    = data_frame.shape[0]  - data_frame_x["1"]
    data_frame_x  = data_frame_x[data_frame_x["feature"] != "coupon_use"]
    
    #count of 1's(yes)
    trace1 = go.Scatterpolar(r = data_frame_x["1"].values.tolist(),
                             theta = data_frame_x["feature"].tolist(),
                             fill  = "toself",name = "count of 1's",
                             mode = "markers+lines",
                             marker = dict(size = 5)
                            )
    #count of 0's(No)
    trace2 = go.Scatterpolar(r = data_frame_x["0"].values.tolist(),
                             theta = data_frame_x["feature"].tolist(),
                             fill  = "toself",name = "count of 0's",
                             mode = "markers+lines",
                             marker = dict(size = 5)
                            ) 
    layout = go.Layout(dict(polar = dict(radialaxis = dict(visible = True,
                                                           side = "counterclockwise",
                                                           showline = True,
                                                           linewidth = 2,
                                                           tickwidth = 2,
                                                           gridcolor = "white",
                                                           gridwidth = 2),
                                         angularaxis = dict(tickfont = dict(size = 10),
                                                            layer = "below traces"
                                                           ),
                                         bgcolor  = "rgb(243,243,243)",
                                        ),
                            paper_bgcolor = "rgb(243,243,243)",
                            title = title,height = 700))
    
    data = [trace2,trace1]
    fig = go.Figure(data=data,layout=layout)
    py.iplot(fig)

#plot
plot_radar(dat_rad,1,"Used -  Customers")
plot_radar(dat_rad,0,"Non Use - Customers")